## This notebook is dedicated to the exploration of the Lyrics dataset


In [2]:
import pandas as pd


In [3]:
#sample_size = 1000  # Desired sample size

lyrics = pd.read_csv('../song_lyrics_reduced.csv')

# Get a random sample of rows
# lyrics = lyrics.sample(n=sample)

# Reset the index if needed
lyrics.reset_index(drop=True, inplace=True)
# lyrics[:10, 1:]

In [166]:
# lyrics

In [167]:
for i in range(len(lyrics[:10])):
    print("This is song - " + lyrics.loc[i, 'lyrics'])

This is song - [Chorus: Opera Steve & Cam'ron]
Killa Cam, Killa Cam, Cam
Killa Cam, Killa Cam
Killa Cam, Cam
Killa Cam, Killa Cam, Cam
Killa Killa Killa Cam
Killa Cam, Cam, Killa (Killa!)
Killa Cam, Killa Cam, Cam (Bases loaded)
Killa Cam, Killa Cam (Uh-huh)
Killa Cam, Cam (Santana on second, Jim on third)
Killa Cam, Killa Cam, Cam (I'm at bat)
Killa Killa Killa Cam
Killa Cam, Cam, Killa (I'm 'bout to hit this shit out the world)
Killa Cam (Ugh, Heatmakerz), Killa Cam, Cam
Killa Cam, Killa Cam
Killa Cam, Cam (Hahahaha)
Killa Cam, Killa Cam, Cam
Killa Killa Killa Cam
Killa Cam, Cam, Killa (We  make this shit clap)
Killa Cam, Killa Cam, Cam
Killa Cam, Killa Cam
Killa Cam, Cam
Killa Cam, Killa Cam, Cam
Killa Killa Killa Cam (Killa! Killa!)
Killa Cam, Cam, Killa
[Verse 1]
With the goons I spar, stay in tune with ma (What up?)
She like, "Damn, this the realest since 'Kumbaya'"
Bomaye, Killa Cam, my Lord (My Lord)
Still the man with the pan, scrilla, fam, on board
Now bitches, they want to n

In [168]:
#lyrics.iloc[:10, 2:8]
# print(lyrics.iat[9,6])

In [5]:
lyrics.iloc[:10]

title  tag     artist  year   views features  \
0                        Can I Live  rap      JAY-Z  1996  468624       {}   
1                 Forgive Me Father  rap   Fabolous  2003    4743       {}   
2                            Fly In  rap  Lil Wayne  2005   78271       {}   
3                  Money On My Mind  rap  Lil Wayne  2005  128927       {}   
4                   Think Yall Know  rap   Fabolous  2003    2530       {}   
5                            DEvils  rap      JAY-Z  1996  504959       {}   
6                      December 4th  rap      JAY-Z  2003  283714       {}   
7                      98 Freestyle  rap      Big L  2000  297788       {}   
8          Its Hot Some Like It Hot  rap      JAY-Z  1999  103549       {}   
9  The Liberation of Lonzo Williams  rap   The Coup  1993     851       {}   

                                              lyrics   id language_cld3  \
0  [Produced by Irv Gotti]\n\n[Intro]\nYeah, hah,...    3            en   
1  Maybe cause I'm eatin\nAnd these bastards fien...    4            en   
2  [Intro]\nSo they ask me\n"Young boy\nWhat you ...    6            en   
3  [Intro]\nYeah\nMoney on my mind, money on my m...   12            en   
4  [Verse 1]\nYou ain't never seen a nigga this l...   13            en   
5  [Produced by DJ Premier]\n\n[Hook Samples: Sno...   14            en   
6  [Produced by Just Blaze]\n\n[Intro: Gloria Car...   15            en   
7  [Verse 1]\nYo, fuck all the glamours and glitz...   16            en   
8  [Produced by Timbaland]\n\n[Verse 1]\nYo, show...   18            en   
9  [Verse 1 - Boots Riley (and E-Roc)]\n1986 a mo...  646            en   

  language_ft language  
0          en       en  
1          en       en  
2          en       en  
3          en       en  
4          en       en  
5          en       en  
6          en       en  
7          en       en  
8          en       en  
9          en       en

# Remove other languages from the dataset
Here we filter out other languages except english

In [169]:
mask = lyrics['language'] == 'en'
filtered_lyrics = lyrics[mask]

# Drop rows with non-English lyrics
filtered_lyrics.drop(filtered_lyrics[~mask].index)
filtered_lyrics.reset_index(inplace=True, drop=True)
lyrics = filtered_lyrics

/var/folders/x9/n8g0lhd50nj2rctpqv0wnvm00000gn/T/ipykernel_96130/1733964651.py:5: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  filtered_lyrics.drop(filtered_lyrics[~mask].index)


In [170]:
print(lyrics.shape)


(3374198, 11)


## Drop all the songs that have features
There is a problem with features, when you look at the songs lyrics the hooks and verses and stuff are assigned to specific authros there, so it means we need to split one song into multiple authors

In [171]:
lyrics = lyrics[lyrics['features'] == '{}']

# Reset the index after dropping rows
lyrics.reset_index(drop=True, inplace=True)

In [6]:
print(lyrics.shape)

(2797631, 11)


In [173]:
# lyrics.to_csv('../song_lyrics_reduced.csv', index=False)


## Explicitness labeling

In [11]:
profanities = set()
with open('../profanities.txt', 'r') as file:
    prof_string = file.read().replace('\n', '')
    prof_tokens = prof_string.split(", ")
    for token in prof_tokens:
        profanities.add(token)

In [12]:
from nltk.tokenize import RegexpTokenizer
from nltk.stem.wordnet import WordNetLemmatizer
lemmatizer = WordNetLemmatizer()
tokenizer = RegexpTokenizer(r'\w+')

def find_explicitness(song):
    tokenized_song = tokenizer.tokenize(song.lower())
    lemmas = (lemmatizer.lemmatize(token) for token in tokenized_song)
    if any(lemma in profanities for lemma in lemmas):
        return 'Explicit content'

    return 'Normal'


In [13]:
from tqdm import tqdm

tqdm.pandas()

lyrics['explicitness'] = lyrics['lyrics'].progress_apply(find_explicitness)

  1%|          | 24150/2797631 [00:45<1:26:29, 534.40it/s]


KeyboardInterrupt: 

## Rhyme extraction
What could be the desired marked formats?
1. Most frequent scheme - ABAB, ABBA (underfitting)
2. The exact words that are being rhymed?
3. The whole rhyming scheme of the song - ABABCDDC-FFFF-ABABCDCD-FFFF-FFFF (overfitting)
4. Multisyllable rhymes - (AB)(AB)(CB)(CB)

# Final Idea
Each song is split into verse and chorus - for each of them we compute the separate rhyming scheme - then we store the whole song scheme

In [119]:
# Specify the file path and name
file_path = '../cmudict.rep'

# Create an empty dictionary to store the word-phoneme mappings
word_phoneme_dict = {}

encodings = ['utf-8', 'latin-1', 'utf-16', 'cp1252']
for encoding in encodings:
    try:
        with open(file_path, 'r') as file:
            for line in file:
                line = line.strip()
                if line:
                    #print(line)
                    split = line.split()
                    word_phoneme_dict[split[0]] = ' '.join(split[1:])
            # break
    except UnicodeDecodeError:
        print('Error')

# Print the dictionary
#print(word_phoneme_dict)

In [120]:
print(word_phoneme_dict.get("ABACUS"))
print(len(word_phoneme_dict))
# print(word_phoneme_dict)

AE1 - B AH0 - K AH0 S
129465


In [121]:
import psutil

# Get the current available memory in bytes
available_memory = psutil.virtual_memory().available

# Convert bytes to human-readable format
available_memory_gb = available_memory / (1024 ** 3)  # Convert bytes to gigabytes

# Print the available memory
print(f"Available Memory: {available_memory_gb:.2f} GB")


Available Memory: 5.40 GB


## Idea
We take each row, take the lyrics from it, split the lyrics by whitespace, remove the special characters, maybe remove some stuff that is in the round brackets (aka low voice stuff), then we take only the last two words in each line, and we annotate them with corresponding phonemes

Algorithm:
1. Split by Chorus - Verse - Hook - Intro - Outro
2. Translate everything into the phonemes
3. Build the scheme for the song
4. Write the scheme to the Dataframe

In [122]:
import re
for index, row in lyrics.iterrows():
    song = row['lyrics']

    # Use regex to find words in square brackets
    matches = re.findall(r'\[([^[\]]+)\]', song)

    # Print the matches
    if matches:
        print(f"Matches in row {index}: {matches}")

Matches in row 0: ['Intro', 'Verse 1: Pimp C', 'Hook', 'Pimp C', 'Hook']
Matches in row 1: ['Chorus', 'Verse 1', 'Chorus', 'Verse 2', 'Chorus', 'Outro']
Matches in row 3: ['Intro', 'Verse']
Matches in row 4: ['Verse 1', 'Pre-Chorus', 'Chorus 1', 'Bagpipes Solo', 'Guitar Solo', 'Verse 2', 'Pre-Chorus', 'Chorus', 'Outro']
Matches in row 5: ['Verse 1', 'Verse 2', 'Chorus', 'Bridge', 'Chorus']
Matches in row 11: ['Intro', 'Verse 1']
Matches in row 12: ['Intro', 'Verse 1: Smokee Tokess', 'Hook: Smokee Tokess', 'Verse 2: Smokee Tokess', 'Hook: Smokee Tokess']
Matches in row 14: ['Verse 1', 'HOOK', 'VERSE 2', 'HOOK']
Matches in row 16: ['Verse 1', 'Verse 2', 'Chorus', 'Verse 3', 'Verse 4', 'Verse 5', 'Chorus', 'Verse 6', 'Verse 7', 'Verse 8', 'Verse 9', 'Verse 10', 'Verse 11', 'Outro']
Matches in row 17: ['Intro', 'Verse', 'Outro']
Matches in row 18: ['Verse 1', 'Hook', 'Verse 2', 'Hook', 'Outro']
Matches in row 19: ['Chorus: Danny', 'Verse 1: Johnny 3 Tears', 'Chorus: Danny', 'Verse 2: Johnn

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



Matches in row 58627: ['Intro', 'Verse 1', 'Verse 2', 'Verse 3']
Matches in row 58628: ['Intro: Phonte', 'Verse 1: Rapper Big Pooh', 'Hook: Rapper Big Pooh', 'Verse 2: Phonte', 'Hook: Rapper Big Pooh', 'Verse 3: Phonte & Rapper Big Pooh', 'Hook: Rapper Big Pooh', 'Outro: Phonte', 'Sample Outro']
Matches in row 58629: ['Intro', 'Verse 1', 'Hook', 'Verse 2', 'Hook/Outro']
Matches in row 58630: ['Intro', 'Verse 1', 'Interlude', 'Verse 2', 'Outro']
Matches in row 58635: ['Verse 1', 'Chorus', 'Verse 2', 'Chorus', 'Outro']
Matches in row 58636: ['Verse 1: Lil Wayne', 'Verse 2:Juelz', 'Outro: Juelz Santana']
Matches in row 58637: ['Chorus x 4', 'Chorus x 4', 'Chorus x 4']
Matches in row 58641: ['?', '?', '?', '?', '?', '?', '?', '?', '?']
Matches in row 58642: ['Verse 1', 'Chorus', 'Verse 2', 'Chorus']
Matches in row 58643: ['Hook', '(Verse)', 'Hook', '(Verse)']
Matches in row 58644: ['Verse 1', 'Hook', 'Verse 2']
Matches in row 58646: ['Verse 1:', 'Hook:', 'Verse 2:', 'Hook']
Matches in row 

In [93]:
print(lyrics.loc[62680, 'artist'])

KeyError: 62680

In [123]:
import re

def separate_lyrics(lyrics):
    parts = ['verse', 'chorus', 'pre-chorus', 'bridge', 'intro', 'outro', 'hook']
    lyrics_parts = {part: [] for part in parts}

    for part in parts:
        pattern = re.compile(r'\s*\({0,2}\[\s*(' + '|'.join(parts) + r')(\s*\d*)?(:\s*\w*\s*)?\]\){0,2}', re.IGNORECASE)
        matches = pattern.findall(lyrics)

        for match in matches:
            # Remove excessive whitespaces and newline characters
            lyrics_parts[part].append(' '.join(match[1].split()))

    return lyrics_parts

# Testing the function
# your lyrics here

lyrics['separated lyrics'] = lyrics['lyrics'].apply(separate_lyrics)

lyrics['separated lyrics'][:10]

# for part in separated_lyrics.keys():
#     print(f"\n{part.upper()}:")
#     for index, lyric in enumerate(separated_lyrics[part]):
#         print(f"\n{part.capitalize()} {index + 1}: {lyric}")

/var/folders/x9/n8g0lhd50nj2rctpqv0wnvm00000gn/T/ipykernel_96130/4025275253.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  lyrics['separated lyrics'] = lyrics['lyrics'].apply(separate_lyrics)


0    {'verse': ['', '', ''], 'chorus': ['', '', '']...
1    {'verse': ['', '1', '', '2', '', ''], 'chorus'...
2    {'verse': [], 'chorus': [], 'pre-chorus': [], ...
3    {'verse': ['', ''], 'chorus': ['', ''], 'pre-c...
4    {'verse': ['1', '', '1', '2', '', '', ''], 'ch...
5    {'verse': ['1', '2', '', '', ''], 'chorus': ['...
6    {'verse': [], 'chorus': [], 'pre-chorus': [], ...
7    {'verse': [], 'chorus': [], 'pre-chorus': [], ...
8    {'verse': [], 'chorus': [], 'pre-chorus': [], ...
9    {'verse': [], 'chorus': [], 'pre-chorus': [], ...
Name: separated lyrics, dtype: object

In [124]:
print(lyrics['lyrics'][0])

[Intro]
I wanna dedicate this song to my momma, knahmtalkinbout?
Happy birthday momma (hey momma, sheeeit) happy birthday
Through all the bullshit niggas tryin to kill us, yup
Yeah, y'knahmsayin? Uhh
The false divorces, child support court (that's right), all that
Nigga droppin out of school you stuck by me knahmtalkinbout?
Thank you... goin to jail
So a lot of motherfuckers be sayin stars up in the sky
But my star right here, that's my angel, knahmtalkinbout?
Check this out

[Verse 1: Pimp C]
I been on top of the world, and been on bottom of the grind
I came through in the fresh cars, playin' surround
I been in the city sellin' crack at the dopefiends
Tryin' to come up Houston be strung out on promethazine
I used to smoke fry, wasn't scared to die
Every day when I wake up I wanted to get high
My momma came and got me from that devil dope
And keep me good even though I used to choose hoes
And sometimes with her older family members a lil' bit wrong
But that's how I came up, makin' rap 

In [107]:
lyrics['separated lyrics'][10]

{'verse': ["You know the shit getting critical Saw 25 years of this wow miracle Blue digital true individual Sleepwalk, teleport this towards lyrical I musical far out cynical 'Cause Papa’s got a brand new bag Of pharmaceuticals So I took a few browse from a different view Hey now sky child come down look at you Its time to excite High episode of life we airtight Its time to excite High episode of life we airtight Oh so empty in need of a friendly pictoral family Take care and mend these ways of my vanity Anything alright warrior don’t cry euphoria’s alright Glorious future"],
 'chorus': [],
 'pre-chorus': [],
 'bridge': [],
 'intro': [],
 'outro': [],
 'hook': []}

In [72]:
def clean_for_rhymes(lyric):
    lyric = re.sub(r'[^A-Za-z0-9\s]', '', lyric) # remove special chars
    lyric = lyric.upper()
    lyric = lyric.split('')
    lyric = lyric.split('\n') # split by new lines
    lyric = list(filter(lambda line: line != '', lyric)) # delete an empty line
    for i, line in enumerate(lyric):
        line = line.split()
        if len(line) >= 2:
            lyric[i] = line[-1] # take the last two words of each line
        else:
            lyric[i] = line

    return lyric


In [73]:
# create a new column in the dataset and apply the cleaning function to it
lyrics['end words'] = lyrics['lyrics'].apply(clean_for_rhymes)

In [74]:
# lyrics['end words'][1000]
for i in range(len(lyrics[100:])):
    print(lyrics['end words'][i])


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



[['SAGAN'], ['FROM', 'SCRATCH'], ['THE', 'UNIVERSE'], ['OF', 'WORMHOLES'], ['IN', 'SPACE'], ['IN', 'TIME'], ['TO', 'US'], ['DESTROY', 'OURSELVES'], ['THE', 'STARS'], ['DAWN', 'AWAITS'], ['GALAXY', 'RISE'], ['BILLION', 'SUNS'], ['MILKY', 'WAY'], ['ELEGANT', 'TRUTHS'], ['EXQUISITE', 'INTERRELATIONSHIPS'], ['OF', 'NATURE'], ['DEPENDS', 'POWERFULLY'], ['THIS', 'COSMOS'], ['OF', 'DUST'], ['MORNING', 'SKY'], ['JUST', 'RECOLLECT'], ['IT', 'ANALYZES'], ['GENERATES', 'ABSTRACTIONS'], ['NUMBER', 'ONE'], ['LOGICAL', 'UNDERPINNING'], ['OWN', 'LANGUAGE'], ['THE', 'WORLD'], ['HAWKING'], ['OF', 'YEARS'], ['THE', 'UNIVERSE'], ['OUT', 'FOREVER'], ['A', 'LIMIT'], ['BLACK', 'HOLES'], ['BIG', 'CRUNCH'], ['UNIVERSE', 'TODAY'], ['SOUNDING', 'IDEAS'], ['SAGAN'], ['THIS', 'TIME'], ['HUMAN', 'HISTORY'], ['OTHER', 'WORLDS'], ['COSMIC', 'OCEAN'], ['WAY', 'OUT'], ['SEEMS', 'INVITING']]
[['LIL', 'MOUSE'], ['NO', 'JOKE'], ['GET', 'SMOKED'], ['GET', 'SMOKED'], ['GET', 'SMOKED'], ['LIL', 'WAYNE'], ['NIGGAS', 'ROLLIN'

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [75]:
# next we make the new function that will use the phoneme dictionary to annotate the phonemes of the words

def translate_to_phonemes(end_words):
    end_words_optimized = []
    for end_word in end_words:
        if len(end_word) == 2:
            end_word_1 = word_phoneme_dict.get(end_word[0])
            end_word_2 = word_phoneme_dict.get(end_word[1])
            end_words_optimized.append([end_word_1, end_word_2])
        elif len(end_word) == 1:
            end_word_1 = word_phoneme_dict.get(end_word[0])
            end_words_optimized.append([end_word_1])
    return end_words_optimized





In [76]:
lyrics['end words phonemes'] = lyrics['end words'].apply(translate_to_phonemes)

In [77]:
lyrics['end words phonemes'][1000]


[['V ER1 S', None],
 ['F AH1 K', 'W IH1 DH'],
 ['L AH1 V', 'W IH1 DH'],
 ['F AH1 K', 'DH IH1 S'],
 ['S T AH1 K', 'W IH1 DH'],
 ['N UW1', 'K L OW1 DH Z'],
 ['D R EH1 S', 'K OW1 D'],
 ['AE1 - D R EH2 S', 'DH OW1 Z'],
 ['Z IH1 P', 'K OW1 D'],
 ['IH1 T', 'R IY1 L'],
 ['SH UH1 D', 'F IY1 L'],
 ['IH1 M', 'R AY1 - M IH0 NG'],
 ['B IH1 L Z', 'D AE1 M'],
 ['S T R EH1 S', 'L OW1'],
 ['B EH1 S T', 'S M OW1 K'],
 ['AH1 V', 'L AO1 - Y ER0 Z'],
 ['EH0 M - P L OY1', 'Y AA1'],
 ['IH1 T S', 'F AH1 - N IY0'],
 ['G EH1 - T IH0 NG', 'M AH1 - N IY0'],
 ['M AY1', 'R EH1 N T'],
 ['SH IH1 T', 'D AE1 M'],
 ['K AE1 N', 'B AY1'],
 ['HH AA1 R D - L IY0', 'S ER0 - P R AY1 Z D'],
 ['DH AE1 T', 'N AY1 T'],
 ['L AY1 F', 'Y EY1'],
 ['HH UH1 K', None],
 ['W IH1 DH', 'M IY1'],
 ['V ER1 S', None],
 ['G OW1 - IH0 NG', 'IH0 N - S EY1 N'],
 ['M AY1', 'L EY1 N'],
 ['DH AH0', 'G EY1 M'],
 ['CH EY1 N JH D', 'D AE1 M'],
 ['IH1 T', 'IH1 Z'],
 ['F AO1 R', 'K IH1 D Z'],
 ['DH EH1 R', 'L IH1 D Z'],
 [None, 'K IH1 S T'],
 ['HH ER0',

In [78]:
lyrics['lyrics'][1000]

"[Verse 1]\nI'm someone you shouldn't fuck with\nI'm the one that these people should fall in love with\nAnd all this pressures got me yelling out man fuck this\nMy old girl prolly wishing she had stuck with\nMoneys coming and I spend it on some new clothes\nLevis snapback SBs that's the dress code\nAnd I'm thinking we should address those\nHating in our area never changing our zip code\nYea, I'm just keeping it real\nIf you think you understand tell me how I should feel\nCuz I've been working I've been grinding every single day I'm rhyming\nAnd the only thing that's changed is my number of bills, damn\nSo I'm just trynna keep my stress low\nMe and my homies we be puffing out the best smoke\nAnd I ain't worried cuz I know plenty of lawyers\nCB do work and they won't even employ ya\nHa I had to laugh cuz its funny\nPutting forty hour weeks so yea I'm getting money\nWill I spend it that depends cuz I got to pay my rent\nQuick getting older getting wiser but I keep on doing dumb shit, dam

## Questions:
1. Some words are not in the dictionary - what to do?
2. How to lable the scheme? (practically)

## Remove brackets
Here we remove the brackets from the lyrics, that they can be used by the classifiers


In [51]:
import re
def preprocess(song):
    return re.sub(r'\[\s*.*?\s*\]\n', '', song)

In [53]:
lyrics.loc[:, 'lyrics'] = lyrics.loc[:, 'lyrics'].apply(preprocess)

In [ ]:
print(lyrics.shape)

In [ ]:
lyrics

## Topic Modelling and Extraction
Current experiment is hold with BERTopic

In [ ]:
lyrics['lyrics']

In [ ]:
import spacy
# from bertopic import BERTopic
# from bertopic.representation import KeyBERTInspired



In [ ]:
# from sklearn.datasets import fetch_20newsgroups
# from tqdm import tqdm
#
# docs = fetch_20newsgroups(subset='test',  remove=('headers', 'footers', 'quotes'))['data']
# nlp = spacy.load('en_core_web_sm', exclude=['tagger', 'parser', 'ner', 'attribute_ruler', 'lemmatizer'])
#
# topic_model = BERTopic(embedding_model=nlp)
# with tqdm(total=len(docs), desc="Fitting topic model") as pbar:
#     topics, probs = tqdm(topic_model.fit_transform(docs), total=len(docs), leave=False)
#
# fig = topic_model.visualize_topics()
# fig.show()

In [ ]:
# from tqdm import tqdm
# docs = lyrics['lyrics']
# nlp = spacy.load('en_core_web_md', exclude=['tagger', 'parser', 'ner', 'attribute_ruler', 'lemmatizer'])
#
# representation_model = KeyBERTInspired()
# topic_model = BERTopic(embedding_model=nlp, representation_model=representation_model)
# with tqdm(total=len(docs), desc="Fitting topic model") as pbar:
#     topics, probs = tqdm(topic_model.fit_transform(docs), total=len(docs), leave=False)
#
# # topics, probs = topic_model.fit_transform(docs)
# fig = topic_model.visualize_topics()
# fig.show()

In [ ]:
# def preprocess_topics(lyric):
#     return remove_stop_words(lyric).replace('\n', '.')
# def remove_stop_words(document):
#     nlp = spacy.load('en_core_web_sm')
#
#     # Tokenize the document using spaCy
#     doc = nlp(document)
#
#     # Remove stop words
#     filtered_tokens = [token.text for token in doc if not token.is_stop]
#
#     # Join the filtered tokens back into a single document
#     filtered_document = ' '.join(filtered_tokens)
#
#     return filtered_document


In [ ]:

import pytextrank
#
# # example text
# print(lyrics['lyrics'][1000])
# text = preprocess_topics(lyrics['lyrics'][1000])
#
#
#
# print(text)
# # load a spaCy model, depending on language, scale, etc.
# nlp = spacy.load("en_core_web_sm")
#
# # add PyTextRank to the spaCy pipeline
# nlp.add_pipe("textrank")
# doc = nlp(text)
#
#
# # examine the top-ranked phrases in the document
# for phrase in doc._.phrases:
#     print(phrase.text)
#     print(phrase.rank, phrase.count)
#     print(phrase.chunks)

In [ ]:
# from icecream import ic
# tr = doc._.textrank
# for sent in tr.summary(limit_phrases=15, limit_sentences=5):
#     ic(sent)

In [ ]:
lyrics


# Following the tutorial on Medium

In [ ]:
# from nltk.stem import WordNetLemmatizer
# from gensim.utils import simple_preprocess
# from gensim.parsing.preprocessing import STOPWORDS
# from nltk.stem.porter import *
# from gensim.corpora import Dictionary
# from gensim.models import TfidfModel, LdaMulticore
# import gensim
#
#
# len(STOPWORDS)
# stopwords = set(STOPWORDS)
# stopwords.update(["yeah", "oh", "ya", "let"])
# len(stopwords)
#
#
# def lemmatization_stemming(text):
#     wnl = WordNetLemmatizer()
#     lemmatization = wnl.lemmatize(text, pos='n')
#
#     stemmer = PorterStemmer()
#     stemming = stemmer.stem(lemmatization)
#     return stemming
#
#
# def text_preprocess(text):
#     result = []
#     for token in simple_preprocess(text):
#         if token not in stopwords and len(token) > 3:
#             result.append(lemmatization_stemming(token))
#     return result
#
#
# processed_lyrics = lyrics['lyrics'].map(text_preprocess)
#
#
# dictionary = Dictionary(processed_lyrics)
# dictionary.filter_extremes()
#
#
# bow_corpus = [dictionary.doc2bow(doc) for doc in processed_lyrics]
#
# tfidf_model = TfidfModel(bow_corpus)
# tfidf_corpus = tfidf_model[bow_corpus]

In [ ]:
import pyLDAvis
import pyLDAvis.gensim

In [ ]:
# lda_model3 = gensim.models.ldamodel.LdaModel(tfidf_corpus, num_topics=5, id2word=dictionary)
# for idx, topic in lda_model3.print_topics(-1):
#     print('Topic: {} \nWords: {}'.format(idx, topic))

In [ ]:
# pyLDAvis.enable_notebook()
# id2word = dictionary
# vis = pyLDAvis.gensim.prepare(lda_model3, tfidf_corpus, id2word)
# vis

# Second Tutorial
from here -https://tim-denzler.medium.com/whats-in-a-song-using-lda-to-find-topics-in-over-120-000-songs-53785767b692

Step 1 - tokenize the lyrics

In [ ]:
from nltk.tokenize import RegexpTokenizer
lyric_corpus = lyrics['lyrics']
lyric_corpus_tokenized = []
tokenizer = RegexpTokenizer(r'\w+')
for lyric in lyric_corpus:
    tokenized_lyric = tokenizer.tokenize(lyric.lower())
    lyric_corpus_tokenized.append(tokenized_lyric)

Step 2 - remove words of size less than 2, remove the numerical values

In [ ]:
for s,song in enumerate(lyric_corpus_tokenized):
    filtered_song = []
    for token in song:
        if len(token) > 2 and not token.isnumeric():
            filtered_song.append(token)
    lyric_corpus_tokenized[s] = filtered_song

Step 3 - Lemmatize everything

In [ ]:
from nltk.stem.wordnet import WordNetLemmatizer
lemmatizer = WordNetLemmatizer()
for s,song in enumerate(lyric_corpus_tokenized):
    lemmatized_tokens = []
    for token in song:
        lemmatized_tokens.append(lemmatizer.lemmatize(token))
    lyric_corpus_tokenized[s] = lemmatized_tokens

Step 4 - remove stop words, remove profanities

In [ ]:
from nltk.corpus import stopwords
stop_words = stopwords.words('english')
new_stop_words = ['ooh','yeah','hey','whoa','woah', 'ohh', 'was', 'mmm', 'oooh','yah','yeh','mmm', 'hmm','deh','doh','jah','wa']
stop_words.extend(new_stop_words)
for s,song in enumerate(lyric_corpus_tokenized):
    filtered_text = []
    for token in song:
        if token not in stop_words:
            filtered_text.append(token)
    lyric_corpus_tokenized[s] = filtered_text

for i in range(10):
    print(lyric_corpus_tokenized[i])

In [ ]:
for i in range(10):
    print(lyric_corpus_tokenized[i])

In [ ]:
profanities = []
with open('../profanities.txt', 'r') as file:
    prof_string = file.read().replace('\n', '')
    prof_tokens = prof_string.split(", ")
    for token in prof_tokens:
        profanities.append(token)
for s,song in enumerate(lyric_corpus_tokenized):
    filtered_text = []
    for token in song:
        if token not in profanities:
            filtered_text.append(token)
    lyric_corpus_tokenized[s] = filtered_text

Step 6 - remove the words that rarely occur in the lyrics

In [ ]:
from gensim.corpora import Dictionary
dictionary = Dictionary(lyric_corpus_tokenized) # we make a dictionary out of it
dictionary.filter_extremes(no_below = 100, no_above = 0.8)

Step 7 - make a bag of words for each of the songs

In [ ]:
from gensim.corpora import MmCorpus
gensim_corpus = [dictionary.doc2bow(song) for song in lyric_corpus_tokenized]
temp = dictionary[0]
id2word = dictionary.id2token

Step 8 - actual model training


In [ ]:
from gensim.models import LdaModel
from tqdm import tqdm
chunksize = 2000
passes = 50
iterations = 400
num_topics = 8



with tqdm(total=num_topics, desc="Training LDA Model") as pbar:
    lda_model = LdaModel(
        corpus=gensim_corpus,
        id2word=id2word,
        chunksize=chunksize,
        alpha='auto',
        eta='auto',
        iterations=iterations,
        num_topics=num_topics,
        passes=passes
    )

In [ ]:
import pyLDAvis
import pyLDAvis.gensim_models as gensimvis
vis_data = gensimvis.prepare(lda_model, gensim_corpus, dictionary)
pyLDAvis.display(vis_data)
pyLDAvis.save_html(vis_data, './Lyrics_LDA_k_'+ str(num_topics) +'.html')

## Affect labeling
Idea here is to use NRC labels and use majority score


In [ ]:
import numpy as np
# Specify the file path and name
file_path = '../NRC-VAD-Lexicon/BipolarScale/NRC-VAD-Lexicon.txt'

# Create an empty dictionary to store the word-phoneme mappings
affect_dictionary = {}

encodings = ['utf-8', 'latin-1', 'utf-16', 'cp1252']
for encoding in encodings:
    try:
        with open(file_path, 'r') as file:
            for line in file:
                line = line.strip()
                if line:
                    #print(line)
                    split = line.split()
                    if len(split) == 4:
                        affect_dictionary[split[0]] = np.array([float(split[1]), float(split[2]), float(split[3])])
                    elif len(split) == 5:
                        affect_dictionary[split[0]+" "+split[1]] = np.array([float(split[2]), float(split[3]), float(split[4])])
                    else:
                        affect_dictionary[split[0]+ " "+split[1]+ " "+split[2]] = np.array([float(split[3]), float(split[4]), float(split[5])])
            # break
    except UnicodeDecodeError:
        print('Error')


In [ ]:
print(affect_dictionary.get('love'))
print(len(affect_dictionary))

Here the algorithm is easy, first we take the lyrics, clean it from the newline characters, split it into words, then we iterate through the words and calculate the majority score. If the word is present in the affect dictionary - we take it, if not- ciao bambino!

In [ ]:
import numpy as np
def compute_affect(lyric):
    lyric = re.sub(r'[^A-Za-z0-9\s]', '', lyric) # remove special chars
    lyric = lyric.lower()
    lyric = lyric.split('\n') # split by new lines
    lyric = list(filter(lambda line: line != '', lyric)) # delete an empty line
    majority_score = np.zeros(3)
    count_of_words = 0
    for i, line in enumerate(lyric):
        line = line.split()
        for word in line:
            if word in affect_dictionary.keys():
                majority_score += affect_dictionary.get(word)
                count_of_words+= 1
    # print(count_of_words)
    return majority_score / count_of_words



In [ ]:
lyrics['affect majority score'] = lyrics['lyrics'].apply(compute_affect)


In [ ]:
lyrics['affect majority score'][9]

# Algorithm
Each song is parsed, each word is checked if it is in the dictionary, if it is - it is added to the aggregate value of the song, finally, this aggregate value is divided by amount of words from the song that are present in the dicitonary. Example - {12, -15, 10} - 5 words - hence {12/5, -15/5, 10/5}

In [ ]:
lyrics

In [ ]:
import matplotlib.pyplot as plt
import numpy as np

vectors = lyrics['affect majority score'].values

# Preprocess the vectors and convert to a valid NumPy array
processed_vectors = []
for vector in vectors:
    # Check if the vector is a valid three-dimensional array
    if isinstance(vector, np.ndarray) and vector.shape == (3,):
        processed_vectors.append(vector)

# Convert the processed vectors to a NumPy array
vectors_array = np.array(processed_vectors)

# Extract the x, y, and z components from the vectors array
valence = vectors_array[:, 0]
arousal = vectors_array[:, 1]
dominance = vectors_array[:, 2]

# Plot the vectors
fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')
ax.plot(valence, arousal, dominance, 'bo')
ax.scatter(valence, arousal, dominance, color='r')

# Set labels for each axis
ax.set_xlabel('valence')
ax.set_ylabel('arousal')
ax.set_zlabel('dominance')

# Show the plot
plt.show()
